## Proyecto 1 - Etapa 1

### Integrantes

- Nicolas Diaz Montaña / n.diaz9 / 202021006
- Sebastian Casanova
- Julio Peña
   

## 1. Importacion de librerias  y Carga de Datos

In [1]:
%pip install num2words
%pip install ydata-profiling
%pip install pattern

Note: you may need to restart the kernel to use updated packages.


Note: you may need to restart the kernel to use updated packages.


Note: you may need to restart the kernel to use updated packages.


In [2]:
import numpy as np
import pandas as pd

from matplotlib import pyplot as plt
import num2words
import re, unicodedata, inflect
import nltk
from pattern.es import parse, split
from gensim.models import Word2Vec
from nltk import word_tokenize, sent_tokenize
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize

from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.metrics import (
    ConfusionMatrixDisplay, RocCurveDisplay,
    roc_auc_score, precision_score, recall_score, f1_score
)
from sklearn.model_selection import train_test_split, RandomizedSearchCV
from sklearn.pipeline import Pipeline
from sklearn.model_selection import train_test_split
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC
from sklearn.metrics import classification_report
from ydata_profiling import ProfileReport

In [3]:
import warnings
warnings.filterwarnings("ignore")

In [4]:
import matplotlib.pyplot as plt

In [5]:
PRINT_RECALL = "Recall:"
PRINT_PRECISION = "Precision:"
PRINT_F1 = "F1:"

In [6]:
# Configuring pandas to show all cell content
pd.set_option("display.max_colwidth", None)

In [7]:
# Downloading stopwords
nltk.download("punkt")
nltk.download("stopwords")
stop_words = stopwords.words("spanish")

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\nicod\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\nicod\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [8]:
stop_words

['de',
 'la',
 'que',
 'el',
 'en',
 'y',
 'a',
 'los',
 'del',
 'se',
 'las',
 'por',
 'un',
 'para',
 'con',
 'no',
 'una',
 'su',
 'al',
 'lo',
 'como',
 'más',
 'pero',
 'sus',
 'le',
 'ya',
 'o',
 'este',
 'sí',
 'porque',
 'esta',
 'entre',
 'cuando',
 'muy',
 'sin',
 'sobre',
 'también',
 'me',
 'hasta',
 'hay',
 'donde',
 'quien',
 'desde',
 'todo',
 'nos',
 'durante',
 'todos',
 'uno',
 'les',
 'ni',
 'contra',
 'otros',
 'ese',
 'eso',
 'ante',
 'ellos',
 'e',
 'esto',
 'mí',
 'antes',
 'algunos',
 'qué',
 'unos',
 'yo',
 'otro',
 'otras',
 'otra',
 'él',
 'tanto',
 'esa',
 'estos',
 'mucho',
 'quienes',
 'nada',
 'muchos',
 'cual',
 'poco',
 'ella',
 'estar',
 'estas',
 'algunas',
 'algo',
 'nosotros',
 'mi',
 'mis',
 'tú',
 'te',
 'ti',
 'tu',
 'tus',
 'ellas',
 'nosotras',
 'vosotros',
 'vosotras',
 'os',
 'mío',
 'mía',
 'míos',
 'mías',
 'tuyo',
 'tuya',
 'tuyos',
 'tuyas',
 'suyo',
 'suya',
 'suyos',
 'suyas',
 'nuestro',
 'nuestra',
 'nuestros',
 'nuestras',
 'vuestro'

In [9]:
reviews_df = pd.read_csv("./data/tipo1_entrenamiento_estudiantes.csv")

#### 1.1 Entendimiento de Datos

In [10]:
reviews_df.shape

(7875, 2)

In [11]:
reviews_df.sample(5)

Review  \
3373                                                                                                                                                                                                                  Los disfraces y bailarines eran geniales! Los cantantes también eran buenas. Acabamos de estar cerca de la parte trasera, así que no pudimos verlo todo! Decepcionante cómo las mesas están dispuestas. Que en realidad gire sus sillas para ver y no tener una vista clara. Asegúrese de que usted es muy temprano para estar más cerca. El ron y cigarros gratis era una delicia.   
5254                                                                                                                                                                                                                                                                            Excelente ubicación, justo en el aeropuerto, a 1 min. a pie Si tienes que coger un vuelo temprano, éste sería sin duda la mejor elección. Habitación está limpio, la gente del servicio es amable, la comida en el restaurante es de buena calidad a un precio razonable. Es sólo una pequeña lástima que no hay piscina.   
2627                                                                                                                                                                                                                                                                                                                     Impresionante y única en el mundo.  Interesante escuchar la historia de su transformación de mina de sal a catedral.  Ofrecen recorrido por la mina , ideal para los jóvenes .  Artesanías y recuerdos a buen precio. El recorrido es un poco largo, pero vale la pena visitar .   
7362  Es increible que la marca Quinta Real permita que un hotel utilice su franquicia siendo un hotel de tan mala calidad y servcicio. Las habitaciones cumplen pero no al nivel que esta cadena nos tiene acostumbrados, le falta cuidar los detalles y la decoracion de las mismas, lo peor del hotel es el servicio del restaurante y de room service, no entienden lo que significa servicio y enfoque al cliente, los alimentos son bastante promedio con un pesimo servicio y gran lentitud. Una muy mala experiencia y desgraciademente esto no deberia de occurrir en cadenas de tanto prestigio   
2998                                                                                                                                                                                                                                                                                                                                                                                                                            Recorrer las hermosas calles de la ciudad amurallada, admirar la arquitectura colonial y recordar toda la historia almacenada allí, es un sitio espectacular, recomendado   

      Class  
3373      4  
5254      4  
2627      4  
7362      2  
2998      5

In [12]:
reviews_df["Class"].value_counts(dropna=False, normalize=True)

Class
5    0.298413
4    0.250286
3    0.199111
2    0.148952
1    0.103238
Name: proportion, dtype: float64

In [13]:
textos = reviews_df.copy()
textos['Conteo'] = [len(x) for x in textos['Review']]
textos['Moda'] = [pd.Series(x).value_counts().index[0] for x in textos['Review']]
textos['Max'] = [[max([len(x) for x in i.split(' ')])][0] for i in textos['Review']]
textos['Min'] = [[min([len(x) for x in i.split(' ')])][0] for i in textos['Review']]

# Se realiza un perfilamiento de los datos con la librería pandas profiling
ProfileReport(textos)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [14]:
reviews_df["Review"] = reviews_df["Review"].astype(str)

## 2. Preparacion de Datos

Para poder empezar el pre-procesamiento de los datos es recomendable realizar las siguientes etapas: Limpieza de los datos, tokenizar y normalizar.

### 2.1. Limpieza de los datos

Para empezar toca eliminar y remplazar cualquier ruido que nos puede generar informacion poco relevante, o conflictos en el peor de los casos, a la hora de hacer el analisis de texto, tales como: 
* Palabras que no esten en ASCII
* Palabras que tengan mayusculas
* Puntuacion
* Reseñas repetidas
* Palabras Stop

In [15]:
def remove_non_ascii(words):
    """Remueve las palabras que no sean ASCII de una lista de palabras 
    tokenizadas"""
    new_words = []
    for word in words:
        new_word = unicodedata.normalize('NFKD', word).encode('ascii', 'ignore').decode('utf-8', 'ignore')
        new_words.append(new_word)
    return new_words

def to_lowercase(words):
    """Convierte todos los caracteres de una lista de palabras 
    tokenizadas a minusculas"""
    return [word.lower() for word in words]

def remove_punctuation(words):
    """Elimina la puntuacion de una lista de palabras 
    tokenizadas"""
    new_words = []
    for word in words:
        new_word = re.sub(r'[^\w\s]', '', word)
        if new_word != '':
            new_words.append(new_word)
    return new_words

def replace_numbers(words):
    """Reemplaza los números de una lista de palabras tokenizadas por una representación textual"""
    new_words = []
    for word in words:
        try:
            if word.isdigit():
                new_word = num2words(int(word), lang='es')
                new_words.append(new_word)
            else:
                new_words.append(word)
        except ValueError:
            # En caso de que el valor no sea un dígito, simplemente añadir la palabra original
            new_words.append(word)
    return new_words
    
def remove_stopwords(words):
    """Elimina las 'stopwords' de una lista de palabras 
    tokenizadas"""
    return [word for word in words if word not in stop_words]

def preprocessing(words):
    words = to_lowercase(words)
    # words = replace_numbers(words)
    words = remove_punctuation(words)
    words = remove_non_ascii(words)
    words = remove_stopwords(words)
    return words

In [16]:
reviews_df.duplicated().any()

True

In [17]:
reviews_df_final = reviews_df.drop_duplicates()

In [18]:
reviews_df_final.duplicated().any()

False

### 2.2. Normalizacion

Toca tomar en cuenta que hay varios aspectos de la normalizacion que pueden hacer parte de la limpieza de datos, y viceversa. En nuestro caso, simplemente se hara lemmatizacion debido a que tiene en cuenta el contexto y la gramática del texto para encontrar la forma base o lema de una palabra. Esto ayuda a preservar el significado original de las palabras, lo que puede ser crucial para comprender las opiniones expresadas en las reseñas. Ademas, de que ayuda a reducir la variabilidad léxica y a capturar de manera más efectiva las características importantes de los lugares turísticos.

In [19]:
def stem_words(words):
    """Stem words in list of tokenized words"""
    stemmer = nltk.stem.SnowballStemmer('spanish')
    stems = []
    for word in words:
        stem = stemmer.stem(word)
        stems.append(stem)
    return stems

def lemmatize_verbs(words):
    """Lemmatize verbs in list of tokenized words"""
    lemmatizer = nltk.WordNetLemmatizer()
    lemmas = []
    for word in words:
        lemma = lemmatizer.lemmatize(word, pos='v')
        lemmas.append(lemma)
    return lemmas

def normalize(words):
    words = lemmatize_verbs(words)
    # words = stem_words(words)
    return words

### 2.3. Tokenizacion

Separar las frases en palabras por medio de apply y una función que tokeniza. Una vez toquenizado se aplican las funciones de limpieza de datos y normalizacion. 

In [20]:
reviews_df_final["Review"] = reviews_df_final["Review"].apply(word_tokenize).apply(preprocessing).apply(normalize).apply(" ".join)
reviews_df_final.sample(5)

Review  \
7497                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           monserrate visita indudablemente debe plan viajen bogota historia excelente vista ciudad   
6798                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       mala experiencia aqui continuamente presionado ir excursiones etc oficial gobierno guiado seguido bar incluso despues decir queriamos tour pusieron agresivos intentamos salir arruino experiencia mila catedral si preciosa gratis mas pequeno esperabamojitos bar ernest hemingway agradable vale pena probar si usted suficientemente valiente esquivar vendedores volveria mero hecho guias agresivas excursion considero puesta turistas tratado tecnicas venta agresivas confianza lugares cairo experiencia nivel i sensacion izquierdo destaco mostro reacio explorar habana mas despues experiencia   
1271  empezar opinion decir 6 dias medellin maravilloso gente agradable guatape barco rumbero visita obligada cartagena bocagrande 5 dias pensando iba ser viaje relajarse asi mejor sitio bonito buenas playas arquitectura bonitalo peor nunca vida tan acosado cada 2 minutos exageracion teniamos persona intentando vendernos viajes cocteles gafas forma intrusiva si decias pues intentaban saber seguir hablando si quedabas callado decian serio asi puede disfrutar ciudad peor tenias sensacion iban timar quitaban todas ganas ir buscar excursiones comprar algun recuerdoun dia playa habia casi nadie solo vendedores empezaron acosar si queriamos tumbona dijimos volvimos toal

In [21]:
textos = reviews_df_final.copy()
textos['Conteo'] = [len(x) for x in textos['Review']]
textos['Moda'] = [pd.Series(x).value_counts().index[0] for x in textos['Review']]
textos['Max'] = [[max([len(x) for x in i.split(' ')])][0] for i in textos['Review']]
textos['Min'] = [[min([len(x) for x in i.split(' ')])][0] for i in textos['Review']]

# Se realiza un perfilamiento de los datos con la librería pandas profiling
ProfileReport(textos)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [22]:
stop_words.append("si")
stop_words.append("ser")
stop_words.append("alli")
stop_words.append("cada")
stop_words.append("ir")
stop_words.append("do")
stop_words.append("asi")
stop_words.append("unas")

In [23]:
reviews_df_final["Review"] = reviews_df_final["Review"].apply(word_tokenize).apply(remove_stopwords).apply(" ".join)

In [24]:
reviews_df_final.sample(5)

Review  \
3597                                                                                                                                                                                                                                                                                                                                                                                                             atractiva ciudad amurallada caminarla perderse call bueno realizar algun tour inicial comenten historia ciudad   
4721  acabamos regresar vacaciones caya coco melia caya coco pasamos semanas agradables mientras estabamos decidimos viajar habana experimentar fantastica ciudad representante recomendo hotel mejor habana comodidad ubicacion viaje esperabamos hotel hotel grande llamativo habitacion bastante aceptable vistas mar aunque cama parte solo tenia tres patas cobran incluyendo cafe habitacion precios bebidas comida altos comida aparte restaurante italiano pobre ensalada vestidor 800 almuerzo desayuno desastre total   
5387                                                                         hoteles mas viejos cartagena bien conservado refaccionado habitaciones grandes comodas toco vista mar hermosa patio hotel pueden encontrar tucanes papagayos desayunos abundantes variados pileta excelente quiere puede cruzar calle metros playa hotel ofrece camastros sombrillas cerca playa 50 mts costa aprox menu dentro restaurant barato digamos mas recomendable comer hotel habitaciones caja seguridad hotel clasico vale pena conocer   
4851                                                                                                                                                                                                                                                                                                                                                                                                                                  cenamos lugar creo decoracion exagerado lugar turistico comida bien estilo yucatan volver   
2731                                                                                                                                                                                                                                                                                                                                                                                                         posicion malecon hace atractivo calidad precio vale pena nota masividad clientes hace platos salgan calidad cobran   

      Class  
3597      5  
4721      1  
5387      4  
4851      2  
2731      2

In [25]:
textos = reviews_df_final.copy()
textos['Conteo'] = [len(x) for x in textos['Review']]
textos['Moda'] = [pd.Series(x).value_counts().index[0] for x in textos['Review']]
textos['Max'] = [[max([len(x) for x in i.split(' ')])][0] for i in textos['Review']]
textos['Min'] = [[min([len(x) for x in i.split(' ')])][0] for i in textos['Review']]

# Se realiza un perfilamiento de los datos con la librería pandas profiling
ProfileReport(textos)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## 3. Entrenamiento

In [26]:
# The param 'stratify' is useful to guarantee label proportions on train and test sets
X_train, X_test, y_train, y_test = train_test_split(reviews_df_final[["Review"]], reviews_df_final["Class"], test_size=0.3, stratify=reviews_df_final["Class"], random_state=1)

In [27]:
X_train_tokens = [nltk.word_tokenize(text) for text in X_train]
X_test_tokens = [nltk.word_tokenize(text) for text in X_test]

In [28]:
X_train.shape, X_test.shape

((5462, 1), (2342, 1))

In [29]:
pd.Series(y_train).value_counts(normalize=True)

Class
5    0.299707
4    0.251556
3    0.199011
2    0.148663
1    0.101062
Name: proportion, dtype: float64

In [30]:
pd.Series(y_test).value_counts(normalize=True)

Class
5    0.299744
4    0.251494
3    0.198975
2    0.148591
1    0.101196
Name: proportion, dtype: float64

## 4.  Vectorizacion de Texto

In [31]:
bow = CountVectorizer(tokenizer=word_tokenize, stop_words=stop_words, lowercase=True)

In [32]:
X_bow = bow.fit_transform(X_train["Review"])

In [33]:
print("Vocabulary size:", len(bow.vocabulary_))

Vocabulary size: 21325


In [34]:
tfidf = TfidfVectorizer(tokenizer=word_tokenize, stop_words=stop_words, lowercase=True)

In [35]:
X_tfidf = tfidf.fit_transform(X_train["Review"])

In [36]:
print("Vocabulary size:", len(tfidf.vocabulary_))

Vocabulary size: 21325


## 5. Modelos y Algoritmos

### 5.1. Modelo TF-IDF (Nicolas Diaz Montaña)

El modelo TF-IDF (Term Frequency-Inverse Document Frequency) es una técnica utilizada en el procesamiento de lenguaje natural (NLP) para analizar la importancia de una palabra en un documento en relación con una colección de documentos. Es comúnmente utilizado en tareas de minería de texto, recuperación de información y clasificación de texto. En el contexto del negocio, TF-IDF puede ser utilizado para identificar las palabras clave y características más relevantes que contribuyen a la evaluación de un lugar turístico.

In [37]:
tfidf_model = RandomForestClassifier(random_state=3)

In [38]:
tfidf_model.fit(X_tfidf, y_train)

RandomForestClassifier(random_state=3)

In [49]:
pd.Series(tfidf_model.feature_importances_, index=tfidf.vocabulary_).sort_values().tail(20).plot.barh(figsize=(20, 20))
plt.show()

In [41]:
tfidf_estimators = tfidf_model.estimators_
print("Number of trees:", len(tfidf_estimators))
print("Trees depth (mean):", np.mean([tree.get_depth() for tree in tfidf_estimators]))

Number of trees: 100
Trees depth (mean): 305.35


In [42]:
y_train_tfidf_predict = tfidf_model.predict(X_tfidf)
y_test_tfidf_predict = tfidf_model.predict(tfidf.transform(X_test["Review"]))

In [43]:
ConfusionMatrixDisplay.from_predictions(y_train, y_train_tfidf_predict)

In [44]:
ConfusionMatrixDisplay.from_predictions(y_test, y_test_tfidf_predict)

In [46]:
print(PRINT_PRECISION, precision_score(y_train, y_train_tfidf_predict, average="weighted"))
print(PRINT_RECALL, recall_score(y_train, y_train_tfidf_predict, average="weighted"))
print(PRINT_F1, f1_score(y_train, y_train_tfidf_predict, average="weighted"))

Precision: 1.0
Recall: 1.0
F1: 1.0


In [47]:
print(PRINT_PRECISION, precision_score(y_test, y_test_tfidf_predict, average="weighted"))  
print(PRINT_RECALL, recall_score(y_test, y_test_tfidf_predict, average="weighted"))
print(PRINT_F1, f1_score(y_test, y_test_tfidf_predict, average="weighted"))

Precision: 0.43539328823246176
Recall: 0.43936806148590946
F1: 0.40943532275276456
